In [1]:
from typing import List, Dict
import os
import subprocess
import numpy as np
import pandas as pd
from scipy.optimize import curve_fit
import matplotlib.pyplot as plt
%matplotlib notebook

In [44]:
%run src/utils.py

In [3]:
SAMPLE = 'EY'

# Depois fazer função que lê os parametros físicos de entrada
D0 = 2.5
SMALL_DELTA = 0.1
GAMMA = 267.51289763847808

EXP_FILE = f'db/experimental/carbonates/diffusionall_{SAMPLE}_data.dat'

RWDB = f'PFGSE_NMR_18102023'
SIMS_DIR = f'db/{RWDB}/carbonates'
SIM_DIR = [d for d in os.listdir(SIMS_DIR) if parse_dirname(d)['sample'] == SAMPLE][0]
SIM_DIRPATH = os.path.join(SIMS_DIR, SIM_DIR)

SPHERES_DB = f'db/PFGSE_NMR_rtag=XsphereY'
SPHERES_DIRS = [os.path.join(SPHERES_DB, d) for d in os.listdir(SPHERES_DB) if SAMPLE in parse_dirname(d)['sample']]

In [4]:
# Load experimental results
exp_data = parse_experimental_results(EXP_FILE)

In [13]:
# Load simulation results
sim_info = parse_dirname(SIM_DIR)
pfg_dir = [d for d in os.listdir(SIM_DIRPATH) if 'NMR_pfgse' in d]
timesamples_dir = os.path.join(SIM_DIRPATH, pfg_dir[0], 'timesamples')

results_file = os.path.join(SIM_DIRPATH, pfg_dir[0], 'PFGSE_results.csv')
gradients_file = os.path.join(SIM_DIRPATH, pfg_dir[0], 'PFGSE_gradient.csv')
echoes_files = [os.path.join(timesamples_dir, f) for f in os.listdir(timesamples_dir) if 'echoes' in f]
echoes_files = order_files_by_last_token(echoes_files)

sim_results_data = parse_sim_results(results_file, ['Time','Dmsd','Dsat', 'Dsat(pts)'])
sim_gradients_data = parse_sim_results(gradients_file, ['Gz', 'Kz'])
sim_echoes_data = [parse_sim_results(ef, ['Gradient','NMR_signal(mean)']) for ef in echoes_files]

sim_data = {
    'info': sim_info,
    'results': sim_results_data,
    'gradients': sim_gradients_data,
    'echoes': sim_echoes_data
}

print(sim_data)

{'info': {'sample': 'EY', 'res': '1.00', 'rho': '10.50', 'shift': '2', 'w': '1M', 'ws': '1', 'bc': 'mirror', 'axis': '2', 'snr': '0.00001'}, 'results': {'Time': array([  10.        ,   10.43333333,   10.875     ,   11.33333333,
         11.81666667,   12.325     ,   12.85      ,   13.39166667,
         13.96666667,   14.55833333,   15.18333333,   15.825     ,
         16.5       ,   17.2       ,   17.93333333,   18.7       ,
         19.49166667,   20.325     ,   21.19166667,   22.09166667,
         23.03333333,   24.01666667,   25.03333333,   26.1       ,
         27.21666667,   28.375     ,   29.58333333,   30.84166667,
         32.15833333,   33.525     ,   34.95      ,   36.44166667,
         37.99166667,   39.60833333,   41.3       ,   43.05833333,
         44.89166667,   46.8       ,   48.79166667,   50.875     ,
         53.04166667,   55.3       ,   57.65      ,   60.10833333,
         62.66666667,   65.33333333,   68.11666667,   71.01666667,
         74.04166667,   77.2       

In [11]:
# Load isolated sphere results
spheres_data = []

for sd in SPHERES_DIRS:
    sd_info = parse_dirname(sd)
    sd_info['sample'] = sd_info['sample'].split('=')[-1]
    sd_info['radius'] = float(sd_info['sample'].split('sphere')[-1])
        
    pfg_dir = [os.path.join(sd,d) for d in os.listdir(sd) if 'NMR_pfgse' in d]
    timesamples_dir = os.path.join(pfg_dir[0], 'timesamples')
    
    sd_results_file = os.path.join(pfg_dir[0], 'PFGSE_results.csv')
    sd_gradients_file = os.path.join(pfg_dir[0], 'PFGSE_gradient.csv')
    sd_echoes_files = [os.path.join(timesamples_dir, f) for f in os.listdir(timesamples_dir) if 'echoes' in f]
    sd_echoes_files = order_files_by_last_token(echoes_files)

    sd_results_data = parse_sim_results(sd_results_file, ['Time','Dmsd','Dsat', 'Dsat(pts)'])
    sd_gradients_data = parse_sim_results(sd_gradients_file, ['Gz', 'Kz'])
    sd_echoes_data = [parse_sim_results(ef, ['Gradient','NMR_signal(mean)']) for ef in sd_echoes_files]
    
    sd_data = {
        'info': sd_info,
        'results': sd_results_data,
        'gradients': sd_gradients_data,
        'echoes': sd_echoes_data
    }    
    spheres_data.append(sd_data)

print(spheres_data[0])

{'info': {'sample': 'EYsphere25', 'res': '1.00', 'rho': '10.50', 'shift': '2', 'w': '1M', 'ws': '1', 'bc': 'mirror', 'axis': '2', 'snr': '0.0001', 'radius': 25.0}, 'results': {'Time': array([  10.        ,   10.43333333,   10.875     ,   11.33333333,
         11.81666667,   12.325     ,   12.85      ,   13.39166667,
         13.96666667,   14.55833333,   15.18333333,   15.825     ,
         16.5       ,   17.2       ,   17.93333333,   18.7       ,
         19.49166667,   20.325     ,   21.19166667,   22.09166667,
         23.03333333,   24.01666667,   25.03333333,   26.1       ,
         27.21666667,   28.375     ,   29.58333333,   30.84166667,
         32.15833333,   33.525     ,   34.95      ,   36.44166667,
         37.99166667,   39.60833333,   41.3       ,   43.05833333,
         44.89166667,   46.8       ,   48.79166667,   50.875     ,
         53.04166667,   55.3       ,   57.65      ,   60.10833333,
         62.66666667,   65.33333333,   68.11666667,   71.01666667,
         74.

In [49]:
%run src/utils.py

In [52]:
for i,e in enumerate(sim_data['echoes']):
    Mkt = e['NMR_signal(mean)']
    Kz = sim_data['gradients']['Kz']
    time = sim_data['results']['Time'][i]
    cutoff = sim_data['results']['Dsat(pts)'][i]
    
    Dt_fit = fit_pfg_diffusion(Mkt, Kz, time, SMALL_DELTA, threshold=0.8, min_values=25)
    Dsat = sim_data['results']['Dsat'][i]
    
    print(i, np.abs(Dt_fit - Dsat))

113
0 0.009155583711214055
111
1 0.009101116720978908
109
2 0.008937406117652369
107
3 0.009267397563127
105
4 0.008963101067622326
103
5 0.008874978492592778
101
6 0.008908004799212499
99
7 0.008793436011794054
98
8 0.009174703662990558
96
9 0.008951450500905622
94
10 0.009021918486042058
92
11 0.008693768157439496
91
12 0.009037361448220649
89
13 0.008623044250717804
87
14 0.008310645230186209
86
15 0.008580263501571261
84
16 0.008308895019066176
83
17 0.008401939853910134
81
18 0.007839088403199135
80
19 0.00865990848112852
78
20 0.008138295808373996
77
21 0.0077445612464988045
76
22 0.00787779747730566
74
23 0.007372794174935304
73
24 0.007730059290454783
72
25 0.007943920762422563
70
26 0.007414043819497396
69
27 0.0075754033060631
68
28 0.00772061607507446
66
29 0.0072450889334889634
65
30 0.007439049635660888
64
31 0.0068257370278175244
63
32 0.007116988366667076
62
33 0.0071791771297717855
61
34 0.0074433787497592
60
35 0.006786518963307175
59
36 0.006823403563773978
57
37 0.00